![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo N 2013 Percepção do Estado de Saúde

## Bibliotecas Utilizadas

In [48]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [49]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2013>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2013>")

[1] 222385   1000

## Definição do peso e filtragem de respondentes do questionário

In [50]:
#Selecionando registros válidos para o módulo P e calculando peso amostral - summary de verificação
pns2013.1<- <Coloque aqui o nome do arquivo RDATA> %>% filter(M001==1)
pns2013.1<-pns2013.1 %>% mutate(peso_morador_selec=((V00291*(60202/145572211))))
pns2013.1<-pns2013.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2013.1$peso_morador_selec)

     Min.   1st Qu.    Median      Mean   3rd Qu.      Max. 
 0.004156  0.243959  0.521557  1.000000  1.147413 31.179597 

## Criação de variáveis dos indicadores

In [51]:
#Desfechos - Indicadores

# Autoavaliação de saúde boa ou muito boa - N001P 
pns2013.1 <- pns2013.1 %>% mutate(N001P = if_else(N001 %in% 1:2,1,2,missing=2))
pns2013.1$N001P<-factor(pns2013.1$N001P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$N001P)

# Autoavaliação de saúde ruim ou muito ruim - N002P 
pns2013.1 <- pns2013.1 %>% mutate(N002P = if_else(N001 %in% 4:5,1,2,missing=2))
pns2013.1$N002P<-factor(pns2013.1$N002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2013.1$N002P)

Sim   Não 
39141 21061

Sim   Não 
 3864 56338

## Definições de abrangências

### Situação urbana ou rural

In [52]:
#Situação Urbano ou Rural
pns2013.1 <- pns2013.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2013.1$Sit_Urbano_Rural<-factor(pns2013.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2013.1$Sit_Urbano_Rural)

urbano  rural 
 49245  10957

### Sexo

In [53]:
#Sexo
pns2013.1 <- pns2013.1 %>% rename(Sexo=C006)
pns2013.1$Sexo<-factor(pns2013.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2013.1$Sexo)

Masculino  Feminino 
    25920     34282

### UF

In [54]:
#Estados - UFs
pns2013.1 <- pns2013.1 %>% rename(Unidades_da_Federacao=V0001)
pns2013.1$Unidades_da_Federacao<-factor(pns2013.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2013.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               1694                1814                2586                1591 
               Pará               Amapá           Tocantins            Maranhão 
               2004                1332                1515                1774 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               1804                2560                1691                1943 
         Pernambuco             Alagoas             Sergipe               Bahia 
               2591                1748                1553                2641 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               3779                1724                3486                5305 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3012                1623                2913                1809 
        Mato Grosso               Goiás    Distrito Federal 
               1476                2423                1811

### Grandes Regiões

In [55]:
#Grandes Regiões

pns2013.1 <- pns2013.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2013.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       12536        18305        14294         7548         7519

### Capital

In [56]:
#Capital
pns2013.1<- pns2013.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco `= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2013.1$Capital)

Porto Velho    Rio Branco          Manaus      Boa Vista          Belém 
          1694           1814           2586           1591           2004 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1332           1515           1774           1804           2560 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          1691           1943           2591           1748           1553 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          2641           3779           1724           3486           5305 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3012           1623           2913           1809           1476 
       Goiânia       Brasília 
          2423           1811

### Faixa Etária

In [57]:
#Faixas Etárias
pns2013.1 <-  pns2013.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60, 75,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 a 74 anos","75 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2013.1$faixa_idade) 

18 a 29 anos    30 a 44 anos    45 a 59 anos    60 a 74 anos 75 anos ou mais 
          14321           20242           14462            8290            2887

### Raça

In [58]:
#Raça
pns2013.1 <- pns2013.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))

pns2013.1$Raca<-factor(pns2013.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2013.1$Raca)

Branca  Preta  Parda   NA's 
 24106   5631  29512    953

### Renda per capita

In [59]:
#Rendimento domiciliar per capita
pns2013.1 <-  pns2013.1 %>% drop_na(VDF003) %>% mutate(rend_per_capita=cut(VDF003,
  breaks = c(-Inf,339, 678, 1356, 2034,Inf),
  labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM","2 até 3 SM","Mais de 3 SM"), 
  ordered_result = TRUE, right = TRUE, na.exclude= TRUE))

summary(pns2013.1$rend_per_capita)


Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM 
       14256        17504        15493         5335         7603

### Escolaridade

In [60]:
# Escolaridade
pns2013.1 <- pns2013.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2013.1$gescol<-factor(pns2013.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Sem instrução e fundamental incompleto","Fundamental completo e médio incompleto",
                                           "Médio completo e superior incompleto","Superior completo"))
summary(pns2013.1$gescol)

Sem instrução e fundamental incompleto Fundamental completo e médio incompleto 
                                  24080                                    9212 
   Médio completo e superior incompleto                       Superior completo 
                                  19145                                    7754

## Criando indicadores

### Filtrando base de indicadores

In [61]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2013Nsurvey<- pns2013.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "N001P","N002P",
                                   "C008","V0031","C009", "Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "Capital","faixa_idade", "Raca","rend_per_capita","gescol")
summary(pns2013Nsurvey)

     V0024            UPA_PNS        peso_morador_selec  N001P      
 Min.   :1110011   Min.   :1100001   Min.   : 0.004156   Sim:39133  
 1st Qu.:2210013   1st Qu.:2200075   1st Qu.: 0.243935   Não:21058  
 Median :2951023   Median :2900192   Median : 0.521557              
 Mean   :3035304   Mean   :3007768   Mean   : 1.000020              
 3rd Qu.:4110111   3rd Qu.:4100002   3rd Qu.: 1.147380              
 Max.   :5310220   Max.   :5300180   Max.   :31.179597              
                                                                    
 N002P            C008            V0031            C009      Sit_Urbano_Rural
 Sim: 3864   Min.   : 18.00   Min.   :1.000   Min.   :1.00   urbano:49234    
 Não:56327   1st Qu.: 30.00   1st Qu.:1.000   1st Qu.:1.00   rural :10957    
             Median : 41.00   Median :2.000   Median :3.00                   
             Mean   : 43.32   Mean   :2.308   Mean   :2.61                   
             3rd Qu.: 55.00   3rd Qu.:4.000   3rd Qu.:4.00

### Exporta tabela filtrada com os dados específicos - Módulo N 2013

In [62]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2013Nsurvey, file.path(diretorio_saida, "pns2013Nsurvey.csv"))

### Cria plano amostral complexo

In [63]:
#survey design
desPNSN=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2013Nsurvey)
desPNSN18=subset(desPNSN, C008>=18)
desPNSNC=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2013Nsurvey)
desPNSNC18=subset(desPNSNC, C008>=18 & V0031==1)
desPNSNR18=subset(desPNSN, C008>=18 & C009!=9)

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [64]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [65]:
#Cálculo dos indicadores usando o pacote survey - alterar
ListaIndicadores = c(~N001P,~N002P)
ListaIndicadoresTexto = c("N001P","N002P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~gescol,~Capital)
ListaDominiosTexto = c("sexo","raça","rend_per_capita","fx_idade_18","urb_rur","uf","região","gescol","capital")
ListaTotais = c('Brasil','Capital')
Ano <- "2013"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [66]:
#Cálculo dos indicadores usando o pacote survey
i <- 0
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    for (dominio in ListaDominios){
               if (ListaDominiosTexto[j]=="capital"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNSNC18 , svymean,vartype= c("ci","cv"))
               }else if(ListaDominiosTexto[j]=="raça"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNSNR18 , svymean,vartype= c("ci","cv"))
                  }else{ 
                    dataframe_indicador<-svyby( indicador , dominio , desPNSN18 , svymean,vartype= c("ci","cv"))
               }
               
               dataframe_indicador<-data.frame(dataframe_indicador)
              
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
               
    }
}

#### Criando a tabela pela abrangência total

In [67]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com a abrangencia Brasil e total das capitais

In [68]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        if(total == 'Capital'){
            dataframe_indicador <- svymean(indicador,desPNSNC18)
        }else{
            dataframe_indicador <- svymean(indicador,desPNSN18)
        }
        
       intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano 
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
        
    }
}


#### Unindo tabela de indicadores e de totais

In [69]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [70]:
matrizIndicadores

abr_tipo        abr_nome            Ano  Indicador
Masculino           sexo            Masculino           2013 N001P    
Feminino            sexo            Feminino            2013 N001P    
Branca              raça            Branca              2013 N001P    
Preta               raça            Preta               2013 N001P    
Parda               raça            Parda               2013 N001P    
Até 1/2 SM          rend_per_capita Até 1/2 SM          2013 N001P    
1/2 até 1 SM        rend_per_capita 1/2 até 1 SM        2013 N001P    
1 até 2 SM          rend_per_capita 1 até 2 SM          2013 N001P    
2 até 3 SM          rend_per_capita 2 até 3 SM          2013 N001P    
Mais de 3 SM        rend_per_capita Mais de 3 SM        2013 N001P    
18 a 29 anos        fx_idade_18     18 a 29 anos        2013 N001P    
30 a 44 anos        fx_idade_18     30 a 44 anos        2013 N001P    
45 a 59 anos        fx_idade_18     45 a 59 anos        2013 N001P    
60 a 74 anos        fx_idade_18     60 a 74 anos        2013 N001P    
75 anos ou mais     fx_idade_18     75 anos ou mais     2013 N001P    
urbano              urb_rur         urbano              2013 N001P    
rural               urb_rur         rural               2013 N001P    
Rondônia            uf              Rondônia            2013 N001P    
Acre                uf              Acre                2013 N001P    
Amazonas            uf              Amazonas            2013 N001P    
Roraima             uf              Roraima             2013 N001P    
Pará                uf              Pará                2013 N001P    
Amapá               uf              Amapá               2013 N001P    
Tocantins           uf              Tocantins           2013 N001P    
Maranhão            uf              Maranhão            2013 N001P    
Piauí               uf              Piauí               2013 N001P    
Ceará               uf              Ceará               2013 N001P    
Rio Grande do Norte uf              Rio Grande do Norte 2013 N001P    
Paraíba             uf              Paraíba             2013 N001P    
Pernambuco          uf              Pernambuco          2013 N001P    
⋮                   ⋮               ⋮                   ⋮    ⋮        
Rio Branco 1        capital         Rio Branco          2013 N002P    
Manaus1             capital         Manaus              2013 N002P    
Boa Vista1          capital         Boa Vista           2013 N002P    
Belém1              capital         Belém               2013 N002P    
Macapá1             capital         Macapá              2013 N002P    
Palmas1             capital         Palmas              2013 N002P    
São Luís1           capital         São Luís            2013 N002P    
Teresina1           capital         Teresina            2013 N002P    
Fortaleza1          capital         Fortaleza           2013 N002P    
Natal1              capital         Natal               2013 N002P    
João Pessoa1        capital         João Pessoa         2013 N002P    
Recife1             capital         Recife              2013 N002P    
Maceió1             capital         Maceió              2013 N002P    
Aracaju1            capital         Aracaju             2013 N002P    
Salvador1           capital         Salvador            2013 N002P    
Belo Horizonte1     capital         Belo Horizonte      2013 N002P    
Vitória1            capital         Vitória             2013 N002P    
Rio de Janeiro3     capital         Rio de Janeiro      2013 N002P    
São Paulo2          capital         São Paulo           2013 N002P    
Curitiba1           capital         Curitiba            2013 N002P    
Florianópolis1      capital         Florianópolis       2013 N002P    
Porto Alegre1       capital         Porto Alegre        2013 N002P    
Campo Grande1       capital         Campo Grande        2013 N002P    
Cuiabá1             capital         Cuiabá              2013 N002P    
Goiânia1            capital         Goiânia 

#### Exportando tabela de indicadores calculados - Módulo N 2013

In [71]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2013N_R.csv"),sep = ";",dec = ",",row.names = FALSE)